In [1]:
import pandas as pd
import csv
import time 
import pickle
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
import numpy as np
import sys
sys.path.append("/usr/local/lib/python3.9/site-packages")
# I import sys instead of import bs4 
import matplotlib.pyplot as plt
import seaborn as sns
import re
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PowerTransformer
from time import sleep 
from pandasql import sqldf
from scipy import stats


pd.set_option('display.max_rows', 10000)

In [2]:
df = pd.read_csv('cleanfinal.csv')
df

Unnamed: 0  sold_price   category          main_brand  score size  \
0               0        31.0        Top        Acne Studios    5.0    l   
1               1        31.0        Top        Acne Studios    5.0    s   
2               2        32.0     Bottom        Acne Studios    5.0    s   
3               3        32.0        Top        Acne Studios    5.0   xs   
4               4        35.0   Acceorie        Acne Studios    5.0    l   
...           ...         ...        ...                 ...    ...  ...   
25157       25157       875.0  Outerwear  Yves Saint Laurent    5.0    s   
25158       25158      1010.0   Footwear  Yves Saint Laurent    5.0    l   
25159       25159      1200.0  Outerwear  Yves Saint Laurent    5.0    s   
25160       25160      1200.0  Outerwear  Yves Saint Laurent    5.0    s   
25161       25161      1630.0  Outerwear  Yves Saint Laurent    5.0    m   

        color  genda  condition_encoded      sub_category  
0      Yellow    Men                  2    Short Sleeve T  
1        Grey    Men                  1    Short Sleeve T  
2        Grey    Men                  1             Denim  
3       Brown    Men                  1  Sweathirt Hoodie  
4       Brown    Men                  0              Belt  
...       ...    ...                ...               ...  
25157   Black    Men                  1            Bomber  
25158   Black  Women                  1              Heel  
25159   Black    Men                  1      Light Jacket  
25160   Black    Men                  1      Light Jacket  
25161    Pink    Men                  1            Bomber  

[25162 rows x 10 columns]

In [3]:
df = df.drop("Unnamed: 0", axis=1)
df = df.drop("score", axis=1)

df

sold_price   category          main_brand size   color  genda  \
0            31.0        Top        Acne Studios    l  Yellow    Men   
1            31.0        Top        Acne Studios    s    Grey    Men   
2            32.0     Bottom        Acne Studios    s    Grey    Men   
3            32.0        Top        Acne Studios   xs   Brown    Men   
4            35.0   Acceorie        Acne Studios    l   Brown    Men   
...           ...        ...                 ...  ...     ...    ...   
25157       875.0  Outerwear  Yves Saint Laurent    s   Black    Men   
25158      1010.0   Footwear  Yves Saint Laurent    l   Black  Women   
25159      1200.0  Outerwear  Yves Saint Laurent    s   Black    Men   
25160      1200.0  Outerwear  Yves Saint Laurent    s   Black    Men   
25161      1630.0  Outerwear  Yves Saint Laurent    m    Pink    Men   

       condition_encoded      sub_category  
0                      2    Short Sleeve T  
1                      1    Short Sleeve T  
2                      1             Denim  
3                      1  Sweathirt Hoodie  
4                      0              Belt  
...                  ...               ...  
25157                  1            Bomber  
25158                  1              Heel  
25159                  1      Light Jacket  
25160                  1      Light Jacket  
25161                  1            Bomber  

[25162 rows x 8 columns]

In [4]:
df.color.value_counts()

Black          7382
Blue           4572
White          2392
Brown          2057
Grey           2018
Green          1577
Muticolor      1275
Red            1056
multi_color     809
Yellow          553
Pink            308
Purple          288
Camo            217
Silver          215
Orange          206
Gold            138
Tie dye          56
Checker          43
Name: color, dtype: int64

In [5]:
threshold = 1

# Group DataFrame by Column1 and filter outliers
df_filtered = df.groupby('main_brand').apply(lambda x: x[(np.abs(stats.zscore(x['sold_price'])) < threshold)])

# Reset the index of the filtered DataFrame
df_filtered.reset_index(drop=True, inplace=True)

df_filtered

sold_price   category          main_brand      size   color genda  \
0            32.0     Bottom        Acne Studios         s    Grey   Men   
1            32.0        Top        Acne Studios        xs   Brown   Men   
2            35.0   Acceorie        Acne Studios         l   Brown   Men   
3            35.0     Bottom        Acne Studios         s   Black   Men   
4            35.0     Bottom        Acne Studios         s    Blue   Men   
...           ...        ...                 ...       ...     ...   ...   
22397       241.0   Acceorie  Yves Saint Laurent  ONE SIZE  Silver   Men   
22398       243.0  Outerwear  Yves Saint Laurent         m   Brown   Men   
22399       250.0   Footwear  Yves Saint Laurent         m   White   Men   
22400       260.0        Top  Yves Saint Laurent         l    Blue   Men   
22401       265.0   Footwear  Yves Saint Laurent         s   Brown   Men   

       condition_encoded      sub_category  
0                      1             Denim  
1                      1  Sweathirt Hoodie  
2                      0              Belt  
3                      1             Denim  
4                      1      Cropped Pant  
...                  ...               ...  
22397                  0            Watche  
22398                  1        Heavy Coat  
22399                  0   Low Top Sneaker  
22400                  1     Shirt ButtoUp  
22401                  2              Boot  

[22402 rows x 8 columns]

In [6]:
y = df_filtered['sold_price']
X = df_filtered.drop(['sold_price'], axis = 1)

In [7]:
numericalX = X.select_dtypes(np.number)
categoricalX = X.select_dtypes(np.object)
X.dtypes

/var/folders/3r/vv8m2rv95fz7qh9n60xh60y40000gp/T/ipykernel_18630/3245492017.py:2: DeprecationWarning: `np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  categoricalX = X.select_dtypes(np.object)


category             object
main_brand           object
size                 object
color                object
genda                object
condition_encoded     int64
sub_category         object
dtype: object

In [8]:
from sklearn.preprocessing import OneHotEncoder
encoder = OneHotEncoder(drop='first').fit(categoricalX)
encoded_categorical = encoder.transform(categoricalX).toarray()
encoded_categorical = pd.DataFrame(encoded_categorical)
X = pd.concat([numericalX, encoded_categorical], axis = 1)

In [9]:
X

condition_encoded    0    1    2    3    4    5    6    7    8    9  \
0                      1  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1                      1  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0   
2                      0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3                      1  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4                      1  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...                  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22397                  0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22398                  1  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0   
22399                  0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22400                  1  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0   
22401                  2  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

        10   11   12   13   14   15   16   17   18   19   20   21   22   23  \
0      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
2      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22397  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22398  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22399  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22400  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22401  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

        24   25   26   27   28   29   30   31   32   33   34   35   36   37  \
0      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
2      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22397  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22398  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22399  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22400  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22401  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

        38   39   40   41   42   43   44   45   46   47   48   49   50   51  \
0      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
2      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
22397  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22398  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22399  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22400  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22401  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

        52   53   54   55   56   57   58   59   60   61   62   63   64   65  \
0      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0

In [10]:
encoding_info = encoder.categories_
encoding_info

[array(['Acceorie', 'Bottom', 'Footwear', 'Luggage', 'Outerwear',
        'Tailoring', 'Top'], dtype=object),
 array(['Acne Studios', 'Adidas', 'Anti Social Social Club', 'Avant Garde',
        'Balenciaga', 'Band Tees', 'Bape', 'Burberry', 'Calvin Klein',
        'Champion', 'Converse', 'Dickies', 'Dior', 'Disney',
        'Distressed Denim', 'Dolce & Gabbana', 'Fila', 'Fruit Of The Loom',
        'Gap', 'Gildan', 'Gucci', 'Guess', 'Hanes', 'Harley Davidson',
        'Hawaiian Shirt', 'Hype', 'Hysteric Glamour', 'Issey Miyake',
        'Kanye West', 'Kapital', 'Kapital Kountry', 'Kappa', 'Lacoste',
        'Lee', "Levi's", "Levi's Vintage Clothing", 'Louis Vuitton',
        'Luxury', 'MLB', 'Maison Margiela', 'Mickey Mouse', 'Military',
        'NBA', 'NFL', 'Nike', 'Number (N)ine', 'Off-White', 'Palace',
        'Patagonia', 'Polo Ralph Lauren', 'Prada', 'Puma', 'Ralph Lauren',
        'Reebok', 'Rick Owens', 'Rick Owens Drkshdw', 'Russell Athletic',
        'Saint Laurent Paris', 'S

In [10]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=0)

In [14]:
from sklearn.ensemble import RandomForestRegressor
regressor = RandomForestRegressor(n_estimators = 900, random_state = 60)
regressor.fit(X_train, y_train)

/Users/AnnyY/opt/anaconda3/envs/DA_env/lib/python3.10/site-packages/sklearn/utils/validation.py:1858: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


RandomForestRegressor(n_estimators=900, random_state=60)

In [15]:
y_pred = regressor.predict(X_test)

/Users/AnnyY/opt/anaconda3/envs/DA_env/lib/python3.10/site-packages/sklearn/utils/validation.py:1858: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


In [16]:
qw=pd.DataFrame({'Actual':y_test, 'Predicted':y_pred})
qw

Actual   Predicted
11312    35.0   39.558146
18390    65.0   57.553376
6389     37.0   40.371086
20411   245.0  158.364658
13765   292.0  317.872037
16640   460.0  381.589808
927      70.0  109.973595
9259     70.0   54.345398
8226    165.0  135.034039
9649     32.0   73.576833
7212     89.0   85.741556
1876    178.0  107.850093
8554    207.0  195.745056
7814     83.0  170.694590
16108    37.0   46.710153
11510    55.0   61.567714
11109   250.0  123.674063
18756    58.0   70.686556
9760     45.0   84.085231
154      90.0   69.399352
17386   165.0  185.790174
8305    290.0  166.702053
5476     66.0   55.187430
13755   279.0  180.511442
19097    35.0   66.921806
13382   175.0   92.159059
19141    38.0   38.997323
9421     40.0   55.893748
21884    50.0   63.146985
7641    150.0  113.505363
17712   670.0  514.776800
15826    60.0   62.586389
7375     80.0  159.322917
14880    50.0  161.129085
12618    45.0   82.832095
18374    59.0   51.996270
12899   100.0  125.760913
5792    307.0  259.605260
4763     50.0   47.082954
19145    38.0   44.001759
15030   146.0  171.518395
15436    50.0   51.479511
4770     50.0   51.961472
12698    55.0   76.676098
7731    200.0  123.113114
12806    75.0   59.476806
9692     39.0   53.418707
16720   205.0  298.567865
13575   150.0  209.358054
11736    34.0   93.183119
10225   100.0  319.239387
19322    60.0   40.768748
3960     80.0   93.454922
18627   305.0  135.973704
8039    200.0  128.561742
4879     78.0   52.468582
2057     75.0  103.328741
2158    100.0   70.106255
21315    55.0   85.048691
9626    105.0   74.055934
516      70.0   94.550523
11610    85.0   67.704128
10704   120.0   81.658785
575      80.0  107.172219
18238   155.0   64.787778
20591    57.0   88.554739
21879    48.0   57.179225
4794     55.0   60.357795
8073    225.0  120.041918
3630     40.0   49.082386
13441   220.0  239.907381
12574    40.0   69.925635
882      55.0   87.144926
19224    45.0   45.595060
4610     31.0   68.065661
3507    420.0  188.916571
13525   110.0  122.692561
2574     45.0   58.781025
19775   115.0   71.713743
10532  1250.0  348.568942
9461     45.0   40.160894
17167    62.0   48.856911
6747     45.0   48.417571
308     203.0   72.687788
12077    79.0   70.237716
17371   150.0  190.538597
1190    300.0  196.467483
2069     75.0   91.302550
13872    50.0   47.317745
12521    32.0   44.543854
21951    69.0   90.473905
4592    215.0  142.988889
14484   125.0  150.725452
2834    240.0  130.149740
7781     70.0  156.346278
2044     70.0  101.254259
14597    40.0   58.527475
9445     42.0   56.484188
9573     70.0   59.840296
12633    45.0   54.258733
798     140.0  128.564833
9002     40.0   53.992665
11580    70.0   52.651389
21017    83.0   57.249416
7994    170.0  112.706460
15311   450.0  388.835219
20845    52.0   71.298176
17569   330.0  204.363425
12429    35.0   46.282606
15717    47.0   52.028684
20963    70.0   77.373496
21349    65.0   95.597074
5188     36.0   46.177263
17107    55.0   49.889525
19419    32.0   55.885214
21502   180.0   65.333990
2610     52.0   49.796140
3093     49.0   61.907192
15583    35.0   41.194281
15502    85.0   42.099672
14047   120.0  181.418831
10521  1120.0  538.171159
17762    35.0   69.746911
14645    47.0   70.859147
6929     90.0   75.001944
5297     80.0   51.956124
18548   165.0   98.051759
14362    75.0   90.407829
3182     65.0   37.611401
17979    80.0  108.486141
1583    130.0   73.496220
17269    32.0   44.615932
5291     80.0   57.290609
505      68.0   77.520686
20271   140.0  143.872536
15960    85.0   70.175576
16553   245.0  336.082315
8704    432.0  318.745196
5895     35.0   41.388046
14237    50.0   80.791270
17928    65.0   66.389250
19812    31.0   65.630545
19818    35.0   59.456955
9413     38.0   66.782737
6847     60.0   38.807723
19273    50.0   51.644546
20203   110.0   84.631503
18625   300.0  154.563318
13611   175.0  184.438050
1893    189.0  120.843889
6472     45.0   42.529073
9125     50.0   53.992665
7899    120.0  151.418086
113

In [17]:
# Calculate the absolute errors
errors = abs(y_pred - y_test)
# Print out the mean absolute error (mae)
print('Mean Absolute Error:', round(np.mean(errors), 2), 'degrees.')

# Calculate mean absolute percentage error (MAPE)
mape = 100 * (errors / y_test)
# Calculate and display accuracy
accuracy = 100 - np.mean(mape)
print('Accuracy:', round(accuracy, 2), '%.')

Mean Absolute Error: 40.78 degrees.
Accuracy: 58.96 %.


In [18]:
encoding_info = encoder.categories_
encoding_info

[array(['Acceorie', 'Bottom', 'Footwear', 'Luggage', 'Outerwear',
        'Tailoring', 'Top'], dtype=object),
 array(['Acne Studios', 'Adidas', 'Anti Social Social Club', 'Avant Garde',
        'Balenciaga', 'Band Tees', 'Bape', 'Burberry', 'Calvin Klein',
        'Champion', 'Converse', 'Dickies', 'Dior', 'Disney',
        'Distressed Denim', 'Dolce & Gabbana', 'Fila', 'Fruit Of The Loom',
        'Gap', 'Gildan', 'Gucci', 'Guess', 'Hanes', 'Harley Davidson',
        'Hawaiian Shirt', 'Hype', 'Hysteric Glamour', 'Issey Miyake',
        'Kanye West', 'Kapital', 'Kapital Kountry', 'Kappa', 'Lacoste',
        'Lee', "Levi's", "Levi's Vintage Clothing", 'Louis Vuitton',
        'Luxury', 'MLB', 'Maison Margiela', 'Mickey Mouse', 'Military',
        'NBA', 'NFL', 'Nike', 'Number (N)ine', 'Off-White', 'Palace',
        'Patagonia', 'Polo Ralph Lauren', 'Prada', 'Puma', 'Ralph Lauren',
        'Reebok', 'Rick Owens', 'Rick Owens Drkshdw', 'Russell Athletic',
        'Saint Laurent Paris', 'S

In [20]:
qw['PercentageDiff'] = ((qw['Actual'] - qw['Predicted']) / qw['Predicted']) * 100

# Sort DataFrame in descending order based on percentage difference
qw_sorted = qw.sort_values('PercentageDiff', ascending=False)

qw_sorted

Actual   Predicted  PercentageDiff
16704   810.0  167.076614      384.807527
346     270.0   62.778878      330.080956
10510   950.0  248.963431      281.582144
1383    790.0  207.314847      281.062916
8593    248.0   66.243704      274.375203
333     240.0   64.767111      270.558445
10532  1250.0  348.568942      258.609116
18628   308.0   86.163187      257.461245
21840   290.0   81.611816      255.340700
322     220.0   62.213415      253.621480
21503   180.0   52.226784      244.650741
22390   205.0   62.314500      228.976402
16693   700.0  213.056712      228.551020
20481   528.0  164.005428      221.940565
10725   150.0   47.112800      218.384814
21181   173.0   54.515259      217.342341
10852   164.0   52.116870      214.677376
15320   500.0  159.208958      214.052681
20389   212.0   67.769931      212.823100
3515    465.0  150.251623      209.480849
22401   265.0   86.043192      207.984856
251     145.0   47.083370      207.964360
278     180.0   58.809729      206.071808
272     167.0   54.760926      204.961970
11666   133.0   43.711178      204.269999
340     250.0   83.510889      199.362159
17716   685.0  229.681278      198.239372
10850   158.0   52.984667      198.199479
11208   385.0  129.358167      197.623266
18619   270.0   91.895060      193.813400
11684   155.0   53.125786      191.760388
10458   533.0  182.858564      191.482110
10080   190.0   65.409902      190.475898
18143   150.0   51.783833      189.665694
10523  1159.0  402.971815      187.613167
14103   180.0   62.720802      186.986128
21214   220.0   77.767887      182.893117
4495    138.0   48.849685      182.499262
16022   120.0   42.689902      181.096920
488     145.0   51.724760      180.329963
10518  1075.0  383.674326      180.185545
1861    160.0   57.194089      179.749190
8304    280.0  100.089722      179.749003
308     203.0   72.687788      179.276622
16702   779.0  281.313241      176.915512
5318    135.0   48.803206      176.621169
21502   180.0   65.333990      175.507437
15285   400.0  145.741676      174.458213
11184   350.0  127.939905      173.565938
249     145.0   53.162373      172.749300
13458   245.0   89.924496      172.450791
4602    239.0   88.143022      171.150223
16035   130.0   48.151693      169.980122
19004   156.0   57.851069      169.657936
3512    449.0  166.949413      168.943743
21507   188.0   69.993666      168.595732
11663   129.0   48.832352      164.169132
1036    150.0   57.009083      163.115965
18634   361.0  137.347500      162.836965
22385   199.0   76.135566      161.375872
10435   445.0  172.108724      158.557493
12412   120.0   46.522915      157.937404
16617   400.0  155.612182      157.049284
3522    498.0  194.035419      156.654173
14054   130.0   50.674418      156.539699
8088    240.0   93.575630      156.477034
10854   205.0   80.183124      155.664769
470     110.0   43.098820      155.227407
21169   162.0   63.581296      154.791911
11658   123.0   48.373461      154.271655
15307   440.0  174.235648      152.531560
2461    117.0   46.389901      152.210067
4476    125.0   49.729815      151.358266
15323   500.0  199.943816      150.070250
20729   115.0   46.193112      148.954863
250     145.0   58.260592      148.881781
10517  1039.0  417.785926      148.691958
2462    120.0   48.253921      148.684456
7277    140.0   56.453706      147.990804
11677   148.0   59.726787      147.795013
20405   232.0   93.686393      147.634682
5856    425.0  171.772180      147.420741
242     135.0   54.760926      146.526143
10077   175.0   71.052233      146.297679
18257   262.0  106.391519      146.260232
276     175.0   71.114836      146.080861
295     193.0   78.575442      145.623817
258     150.0   61.084352      145.562072
8297    270.0  110.303725      144.778678
11702   185.0   75.688780      144.421962
14076   145.0   59.541497      143.527634
1029    150.0   61.738730      142.959322
10519  1075.0  443.018796      142.653361
5153    108.0   44.562667      142.355332
316     215.0   8

In [29]:
qw_sorted['index1'] = qw_sorted.index
qw_sorted

Actual   Predicted  PercentageDiff  index1
17716   685.0  132.729145      416.088609   17716
10510   950.0  188.699590      403.445714   10510
16704   810.0  175.393489      361.818738   16704
333     240.0   56.124960      327.617229     333
346     270.0   63.263996      326.783034     346
8593    248.0   60.844947      307.593417    8593
22390   205.0   51.244180      300.045430   22390
14103   180.0   45.223089      298.026765   14103
10532  1250.0  335.691697      272.365481   10532
17661   485.0  132.729145      265.405803   17661
10850   158.0   44.246850      257.087564   10850
3512    449.0  127.016849      253.496408    3512
22385   199.0   56.517787      252.101544   22385
322     220.0   63.443630      246.764524     322
21216   220.0   63.634628      245.723716   21216
20481   528.0  154.759378      241.174800   20481
331     235.0   68.904488      241.051807     331
1383    790.0  232.973283      239.094677    1383
4603    240.0   71.458796      235.857882    4603
21191   185.0   55.098466      235.762526   21191
251     145.0   43.419380      233.952258     251
10518  1075.0  321.955012      233.897582   10518
11684   155.0   46.505988      233.290416   11684
340     250.0   75.227893      232.323543     340
20038   202.0   60.871652      231.845766   20038
11702   185.0   56.095936      229.792160   11702
18605   245.0   74.676239      228.082941   18605
18601   235.0   72.248855      225.264670   18601
22401   265.0   82.089255      222.819351   22401
21214   220.0   68.320331      222.012494   21214
16693   700.0  219.520549      218.876753   16693
3515    465.0  145.972054      218.554125    3515
8304    280.0   89.152330      214.069189    8304
13455   240.0   76.623835      213.218466   13455
20447   320.0  102.466864      212.296080   20447
15253   349.0  112.593333      209.965066   15253
16686   650.0  210.846090      208.281742   16686
12996   170.0   55.563319      205.957244   12996
21503   180.0   59.696456      201.525436   21503
10080   190.0   64.115355      196.340867   10080
21223   235.0   79.694065      194.877668   21223
21169   162.0   55.098466      194.019077   21169
11666   133.0   45.427907      192.771578   11666
11677   148.0   50.573620      192.642688   11677
3507    420.0  143.859409      191.951707    3507
18628   308.0  105.812823      191.080034   18628
488     145.0   49.902286      190.567849     488
4602    239.0   82.551845      189.515030    4602
10725   150.0   51.995608      188.485902   10725
20449   320.0  110.972120      188.360715   20449
11224   430.0  151.423140      183.972449   11224
13458   245.0   87.029177      181.514784   13458
15166   245.0   87.254877      180.786599   15166
20033   195.0   70.241327      177.614347   20033
18625   300.0  108.653340      176.107481   18625
18578   199.0   72.248855      175.436891   18578
15320   500.0  182.386647      174.142876   15320
4495    138.0   50.378945      173.923960    4495
20026   171.0   62.540530      173.422691   20026
21204   200.0   73.760847      171.146560   21204
16022   120.0   44.277794      171.016214   16022
1036    150.0   55.496132      170.289106    1036
15310   450.0  166.599732      170.108478   15310
15309   450.0  166.599732      170.108478   15309
18144   150.0   55.723691      169.185325   18144
18143   150.0   55.781649      168.905641   18143
10852   164.0   61.484404      166.734309   10852
348     270.0  101.414065      166.235261     348
22352   155.0   58.250556      166.091879   22352
18634   361.0  136.848933      163.794530   18634
10458   533.0  202.315927      163.449352   10458
20022   160.0   60.871652      162.848131   20022
10854   205.0   78.015171      162.769404   10854
15214   295.0  112.593333      162.004855   15214
15323   500.0  192.759464      159.390636   15323
321     220.0   84.936377      159.017405     321
3522    498.0  193.631971      157.188933    3522
19004   156.0   60.836176      156.426374   19004
5318    135.0   52.838725      155.494432    5318
1948   

In [31]:
df_filtered['index1'] = df_filtered.index
df_filtered

sold_price   category          main_brand  score      size   color  \
0            32.0     Bottom        Acne Studios    5.0         s    Grey   
1            32.0        Top        Acne Studios    5.0        xs   Brown   
2            35.0   Acceorie        Acne Studios    5.0         l   Brown   
3            35.0     Bottom        Acne Studios    5.0         s   Black   
4            35.0     Bottom        Acne Studios    5.0         s    Blue   
...           ...        ...                 ...    ...       ...     ...   
22397       241.0   Acceorie  Yves Saint Laurent    5.0  ONE SIZE  Silver   
22398       243.0  Outerwear  Yves Saint Laurent    5.0         m   Brown   
22399       250.0   Footwear  Yves Saint Laurent    5.0         m   White   
22400       260.0        Top  Yves Saint Laurent    5.0         l    Blue   
22401       265.0   Footwear  Yves Saint Laurent    5.0         s   Brown   

      genda  condition_encoded  index1  
0       Men                  1       0  
1       Men                  1       1  
2       Men                  0       2  
3       Men                  1       3  
4       Men                  1       4  
...     ...                ...     ...  
22397   Men                  0   22397  
22398   Men                  1   22398  
22399   Men                  0   22399  
22400   Men                  1   22400  
22401   Men                  2   22401  

[22402 rows x 9 columns]

In [41]:
pysqldf = lambda q: sqldf(q, globals())

we = pysqldf("""select *
        from qw_sorted
        left join df_filtered ON qw_sorted.index1 = df_filtered.index1
        where PercentageDiff > 100
        order by PercentageDiff desc


""")


we

Actual   Predicted  PercentageDiff  index1  sold_price   category  \
0     685.0  132.729145      416.088609   17716       685.0   Acceorie   
1     950.0  188.699590      403.445714   10510       950.0     Bottom   
2     810.0  175.393489      361.818738   16704       810.0     Bottom   
3     240.0   56.124960      327.617229     333       240.0        Top   
4     270.0   63.263996      326.783034     346       270.0     Bottom   
5     248.0   60.844947      307.593417    8593       248.0   Acceorie   
6     205.0   51.244180      300.045430   22390       205.0    Luggage   
7     180.0   45.223089      298.026765   14103       180.0        Top   
8    1250.0  335.691697      272.365481   10532      1250.0     Bottom   
9     485.0  132.729145      265.405803   17661       485.0   Acceorie   
10    158.0   44.246850      257.087564   10850       158.0        Top   
11    449.0  127.016849      253.496408    3512       449.0     Bottom   
12    199.0   56.517787      252.101544   22385       199.0        Top   
13    220.0   63.443630      246.764524     322       220.0        Top   
14    220.0   63.634628      245.723716   21216       220.0  Outerwear   
15    528.0  154.759378      241.174800   20481       528.0  Outerwear   
16    235.0   68.904488      241.051807     331       235.0        Top   
17    790.0  232.973283      239.094677    1383       790.0  Outerwear   
18    240.0   71.458796      235.857882    4603       240.0        Top   
19    185.0   55.098466      235.762526   21191       185.0  Outerwear   
20    145.0   43.419380      233.952258     251       145.0        Top   
21   1075.0  321.955012      233.897582   10518      1075.0   Acceorie   
22    155.0   46.505988      233.290416   11684       155.0        Top   
23    250.0   75.227893      232.323543     340       250.0        Top   
24    202.0   60.871652      231.845766   20038       202.0        Top   
25    185.0   56.095936      229.792160   11702       185.0        Top   
26    245.0   74.676239      228.082941   18605       245.0        Top   
27    235.0   72.248855      225.264670   18601       235.0        Top   
28    265.0   82.089255      222.819351   22401       265.0   Footwear   
29    220.0   68.320331      222.012494   21214       220.0  Outerwear   
30    700.0  219.520549      218.876753   16693       700.0   Footwear   
31    465.0  145.972054      218.554125    3515       465.0   Acceorie   
32    280.0   89.152330      214.069189    8304       280.0        Top   
33    240.0   76.623835      213.218466   13455       240.0        Top   
34    320.0  102.466864      212.296080   20447       320.0     Bottom   
35    349.0  112.593333      209.965066   15253       349.0   Acceorie   
36    650.0  210.846090      208.281742   16686       650.0   Footwear   
37    170.0   55.563319      205.957244   12996       170.0  Outerwear   
38    180.0   59.696456      201.525436   21503       180.0        Top   
39    190.0   64.115355      196.340867   10080       190.0     Bottom   
40    235.0   79.694065      194.877668   21223       235.0        Top   
41    162.0   55.098466      194.019077   21169       162.0  Outerwear   
42    133.0   45.427907      192.771578   11666       133.0        Top   
43    148.0   50.573620      192.642688   11677       148.0        Top   
44    420.0  143.859409      191.951707    3507       420.0   Acceorie   
45    308.0  105.812823      191.080034   18628       308.0        Top   
46    145.0   49.902286      190.567849     488       145.0   Footwear   
47    239.0   82.551845      189.515030    4602       239.0     Bottom   
48    150.0   51.995608      188.485902   10725       150.0        Top   
49    320.0  110.972120      188.360715   20449       320.0        Top   
50    430.0  151.423140      183.972449   11224       430.0        Top   
51    245.0   87.029177      181.514784   13458       245.0        Top   
52    245.0   87.254877      180.786599   15166       245.0        Top   
53    195

In [ ]:
we.color.value_counts()

# Save model

In [13]:
Pkl_Filename = "model1.pkl"  

In [20]:
with open(Pkl_Filename, 'wb') as file:  
    pickle.dump(regressor, file)

In [14]:
with open(Pkl_Filename, 'rb') as file:  
    Pickled_regressor = pickle.load(file)

Pickled_regressor

RandomForestRegressor(n_estimators=900, random_state=60)

In [19]:
score = Pickled_regressor.score(X_test, y_test)  
# Print the Score


/Users/AnnyY/opt/anaconda3/envs/DA_env/lib/python3.10/site-packages/sklearn/utils/validation.py:1858: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


In [20]:
print("Test score: {0:.2f} %".format(100 * score))  

# Predict the Labels using the reloaded Model


Test score: 57.59 %


In [22]:
Ypredict = Pickled_regressor.predict(X_test)  

Ypredict

/Users/AnnyY/opt/anaconda3/envs/DA_env/lib/python3.10/site-packages/sklearn/utils/validation.py:1858: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(


array([ 39.3062037 ,  57.53489539,  40.36724968, ..., 414.93488215,
        97.4086918 ,  80.22427778])

# App

In [11]:
from flask import Flask, request, render_template

In [12]:
app = Flask(__name__)

In [13]:
@app.route('/')
def home():
    return render_template('index.html')

data = {
        'category': ['Bottom'],
        'main_brand': ['Acne Studios'],
        'size': ['s'],
        'color': ['Grey'],
        'genda': ['Men'],
        'condition_encoded': [1],
        'sub_category': ['Denim'],
    }

M = pd.DataFrame(data)
M

numericalX = M.select_dtypes(np.number)
categoricalX = M.select_dtypes(np.object)
categoricalX

encoding_info = encoder.categories_
encoding_info

# Obtain the encoding information from the original encoder
encoding_info = encoder.categories_

# Create a new encoder for the new dataset using the same encoding information
new_encoder = OneHotEncoder(categories=encoding_info, drop='first')

# Apply the encoding to the new dataset
new_encoded_data = new_encoder.fit_transform(categoricalX).toarray()

encoded_categorical = pd.DataFrame(new_encoded_data)
T = pd.concat([numericalX, encoded_categorical], axis = 1)
T


Pickled_regressor.predict(T)

In [14]:
@app.route('/predict', methods=['POST'])
def predict():
    # Retrieve the selected options from the form data
    brand = request.form.get('brand')
    color = request.form.get('color')
    condition = request.form.get('condition')
    if condition == 'New':
        condition = 0
    elif condition == 'Gently Used':
        condition = 1
    elif condition == 'Used':
        condition = 2
    else: condition = 3
    size = request.form.get('size')
    gender = request.form.get('gender')
    category = request.form.get('category')
    sub_category = request.form.get('sub_category')

    # Create a dictionary with the selected options
    data = {
                
        'category': [category],
        'main_brand': [brand],
        'size': [size],
        'color': [color],
        'genda': [gender],
        'condition_encoded': [condition],
        'sub_category': [sub_category]
    }

    # Convert the dictionary into a dataframe
    M = pd.DataFrame(data)
    
    numericalX = M.select_dtypes(np.number)
    categoricalX = M.select_dtypes(np.object)
    categoricalX
    
    # Obtain the encoding information from the original encoder
    encoding_info = encoder.categories_

# Create a new encoder for the new dataset using the same encoding information
    new_encoder = OneHotEncoder(categories=encoding_info, drop='first')

# Apply the encoding to the new dataset
    new_encoded_data = new_encoder.fit_transform(categoricalX).toarray()

    encoded_categorical = pd.DataFrame(new_encoded_data)
    T = pd.concat([numericalX, encoded_categorical], axis = 1)
    T
    

    # Load the machine learning model from a pickle file
    with open('model1.pkl', 'rb') as f:
        model = pickle.load(f)

    # Make predictions with the model
    prediction = model.predict(T)

    # Render a template with the prediction result
    return render_template('index.html', prediction_text='Sold price should be {}'.format(prediction))

In [ ]:
if __name__ == "__main__":
    app.run()

 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:5000/ (Press CTRL+C to quit)
127.0.0.1 - - [10/May/2023 00:57:14] "GET / HTTP/1.1" 200 -
/var/folders/3r/vv8m2rv95fz7qh9n60xh60y40000gp/T/ipykernel_18630/736476505.py:35: DeprecationWarning: `np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  categoricalX = M.select_dtypes(np.object)
/Users/AnnyY/opt/anaconda3/envs/DA_env/lib/python3.10/site-packages/sklearn/utils/validation.py:1858: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['int', 'str']. An error will be raised in 1.2.
  warnings.warn(
127.0.0.1 - - [10/May/2023 00:57:39] "POST /predict HTTP/1.1" 200 -
